# Algorithmic Trading Project

    1.   Algorithm Trading (Condition on Indicators)
    2.   Reinforcment Learning AI Trading (AI learns to use Indicators)
    3.   Combining Algorithmic and AI Trading

## Team Members:

    1.   B20AI021 - Mitul Agrawal
    2.   B20AI059 - Suyog Gupta
    3.   B20AI052 - Ayush Abrol
    4.   B20AI026 - Neehal Bajaj
    5.   B20CH015 - Divyanshu Pandey

### Necessary Installs

In [1]:
!pip install pandas_ta
!pip install vectorbt
!pip install yfinance
!pip install quantstats
!pip install nsepy

In [1]:
import pandas as pd
import pandas_ta as ta
import yfinance as yf
import os

from math import modf
import torch
import torch.nn as nn
from torch.nn.modules import module
import torch.optim as optim
import torch.nn.functional as F

import random
import time
import numpy as np
from collections import deque
import vectorbt as vbt
import json
import ta as techa

import warnings
warnings.filterwarnings("ignore")

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

### Data

In [2]:
def getData():
    if os.path.exists('data.csv'):
        df = pd.read_csv('data.csv', index_col=0)
    else:
        df = yf.download('^NSEI', start="2011-01-01", end="2023-12-31", interval="1d")
        df.to_csv('data.csv')

    # print(ta.adx(df['High'], df['Low'], df['Close'], length=14).head(5))
    df['RSI14'] = ta.rsi(df['Close'], length=14)
    df['EMA4'] = ta.ema(df['Close'], length=4)
    df['EMA20'] = ta.ema(df['Close'], length=20)
    df['EMA14'] = ta.ema(df['Close'], length=14)
    df['EMA50'] = ta.ema(df['Close'], length=50)
    df['EMA100'] = ta.ema(df['Close'], length=100)
    df['EMA200'] = ta.ema(df['Close'], length=200)
    df['RSI28'] = ta.rsi(df['Close'], length=28)
    df['MFI14'] = ta.mfi(df['High'], df['Low'], df['Close'], df['Volume'], length=14)
    df['OBV14'] = ta.obv(df['Close'], df['Volume'], length=14)
    df['EMA7OBV14'] = ta.ema(df['OBV14'], length=7)
    df['ADX14'] = ta.adx(df['High'], df['Low'], df['Close'], length=14).iloc[:,0]
    # df['MACD'] = ta.macd(df['Close'], 12, 26, 9).iloc[:,0]
    df['ATR'] = ta.atr(df['High'], df['Low'], df['Close'], length=14)
    df['EMA14ATR'] = ta.ema(df['ATR'], length=14)
    df['RSX14'] = ta.rsx(df['Close'], length=14)
    df['EMA4VOLUME'] = ta.ema(df['Volume'], length=4)
    df['EMA14VOLUME'] = ta.ema(df['Volume'], length=14)
    macd = techa.trend.MACD(df['Close'], 12, 26, 9)
    df["MACD"] = macd.macd()
    df["MACD_SIGNAL"] = macd.macd_signal()
    df["MACD_HISTOGRAM"] = macd.macd_diff()
    # get an upward trend line

    df['up_trend'] = df['Close'].diff() > 0
    df['down_trend'] = df['Close'].diff() < 0
    df.dropna(inplace=True)

    # Prepare state data
    df['State1'] = df['RSI14']/100 - 0.5
    df['State2'] = df['EMA4']/df['EMA20'] - 1
    df['State3'] = df['RSI28']/100 - 0.5
    df['State4'] = df['Close']/df['EMA14'] - 1
    df['State5'] = df['MFI14']/100 - 0.5
    df['State6'] = ((df['OBV14'] - df['EMA7OBV14']) > 0).astype(int) * 2 - 1
    df['State7'] = df['ADX14']/100 - 0.5
    df['State8'] = 10 * df['MACD']/df['Close']
    df['State9'] = 10 * df['Close']/df['Close'].shift(1) - 1
    df['State10'] = df['ATR'] / df['EMA14ATR'] - 1
    df['State11'] = df['RSX14']/100 - 0.5
    df['State12'] = df['EMA4VOLUME']/df['EMA14VOLUME'] - 1
    df['State13'] = df['High']/df['Close'] - 1
    df['State14'] = df['Low']/df['High']
    df['State15'] = (df['Volume']-df['EMA4VOLUME'] > 0).astype(int) * 2 - 1
    df.dropna(inplace=True)

    return df

In [3]:
df = getData()
print(df.head(10))

                   Open         High          Low        Close    Adj Close  \
Date                                                                          
2013-01-22  6080.149902  6101.299805  6040.500000  6048.500000  6048.500000   
2013-01-23  6052.850098  6069.799805  6021.149902  6054.299805  6054.299805   
2013-01-24  6046.200195  6065.299805  6007.850098  6019.350098  6019.350098   
2013-01-25  6024.500000  6080.549805  6014.450195  6074.649902  6074.649902   
2013-01-28  6082.100098  6088.399902  6061.399902  6074.799805  6074.799805   
2013-01-29  6064.700195  6111.799805  6042.450195  6049.899902  6049.899902   
2013-01-30  6065.000000  6071.950195  6044.149902  6055.750000  6055.750000   
2013-01-31  6045.649902  6058.049805  6025.149902  6034.750000  6034.750000   
2013-02-01  6040.950195  6052.950195  5983.200195  5998.899902  5998.899902   
2013-02-04  6025.200195  6038.500000  5981.250000  5987.250000  5987.250000   

            Volume      RSI14         EMA4        E

In [4]:
df

Open          High           Low         Close  \
Date                                                                 
2013-01-22   6080.149902   6101.299805   6040.500000   6048.500000   
2013-01-23   6052.850098   6069.799805   6021.149902   6054.299805   
2013-01-24   6046.200195   6065.299805   6007.850098   6019.350098   
2013-01-25   6024.500000   6080.549805   6014.450195   6074.649902   
2013-01-28   6082.100098   6088.399902   6061.399902   6074.799805   
...                  ...           ...           ...           ...   
2023-12-22  21295.849609  21390.500000  21232.449219  21349.400391   
2023-12-26  21365.199219  21477.150391  21329.449219  21441.349609   
2023-12-27  21497.650391  21675.750000  21495.800781  21654.750000   
2023-12-28  21715.000000  21801.449219  21678.000000  21778.699219   
2023-12-29  21737.650391  21770.300781  21676.900391  21731.400391   

               Adj Close  Volume      RSI14          EMA4         EMA20  \
Date                                                                      
2013-01-22   6048.500000  129000  60.660874   6053.202413   5989.113133   
2013-01-23   6054.299805  137000  61.221277   6053.641370   5995.321387   
2013-01-24   6019.350098  185200  56.040519   6039.924861   5997.609836   
2013-01-25   6074.649902  147600  61.580490   6053.814878   6004.946985   
2013-01-28   6074.799805  113100  61.594619   6062.208848   6011.599635   
...                  ...     ...        ...           ...           ...   
2023-12-22  21349.400391  284700  72.117736  21298.731122  20860.984922   
2023-12-26  21441.349609  219500  73.712515  21355.778517  20916.257749   
2023-12-27  21654.750000  256500  77.000453  21475.367110  20986.590345   
2023-12-28  21778.699219  393100  78.669287  21596.699954  21062.029285   
2023-12-29  21731.400391  270900  76.391413  21650.580128  21125.778914   

                   EMA14  ...  State6    State7    State8    State9   State10  \
Date                      ...                                                   
2013-01-22   6012.390489  ...      -1 -0.208879 -0.088867  8.944429 -0.020078   
2013-01-23   6017.978398  ...       1 -0.215873 -0.086678  9.009589 -0.026272   
2013-01-24   6018.161291  ...      -1 -0.226344 -0.079897  8.942273 -0.021588   
2013-01-25   6025.693106  ...       1 -0.232711 -0.079875  9.091870 -0.008258   
2013-01-28   6032.240666  ...       1 -0.236916 -0.079535  9.000247 -0.039741   
...                  ...  ...     ...       ...       ...       ...       ...   
2023-12-22  21045.644627  ...       1 -0.039903 -0.190567  9.044389  0.139912   
2023-12-26  21098.405291  ...       1 -0.046565 -0.188046  9.043069  0.101117   
2023-12-27  21172.584586  ...       1 -0.047245 -0.190611  9.099527  0.099210   
2023-12-28  21253.399870  ...       1 -0.044834 -0.195348  9.057239  0.067322   
2023-12-29  21317.133273  ...       1 -0.042671 -0.196377  8.978282  0.026564   

             State11   State12   State13   State14  State15  
Date                                                         
2013-01-22  0.136003  1.568070  0.008729  0.990035        1  
2013-01-23  0.131532  1.260230  0.002560  0.991985        1  
2013-01-24  0.113009  1.111653  0.007634  0.990528        1  
2013-01-25  0.103425  0.861015  0.000971  0.989129        1  
2013-01-28  0.099361  0.607791  0.002239  0.995565       -1  
...              ...       ...       ...       ...      ...  
2023-12-22  0.255915 -0.010105  0.001925  0.992611       -1  
2023-12-26  0.226772 -0.080374  0.001670  0.993123       -1  
2023-12-27  0.215877 -0.079500  0.000970  0.991698       -1  
2023-12-28  0.219267  0.051156  0.001045  0.994338        1  
2023-12-29  0.223396  0.005533  0.001790  0.995710       -1  

[2686 rows x 43 columns]

In [249]:
# Save data
df.to_csv('indicator_data.csv')

In [5]:
all_indicators = list(df.columns)

In [81]:
all_indicators

['Open',
 'High',
 'Low',
 'Close',
 'Adj Close',
 'Volume',
 'RSI14',
 'EMA4',
 'EMA20',
 'EMA14',
 'EMA50',
 'EMA100',
 'EMA200',
 'RSI28',
 'MFI14',
 'OBV14',
 'EMA7OBV14',
 'ADX14',
 'ATR',
 'EMA14ATR',
 'RSX14',
 'EMA4VOLUME',
 'EMA14VOLUME',
 'MACD',
 'MACD_SIGNAL',
 'MACD_HISTOGRAM',
 'up_trend',
 'down_trend',
 'State1',
 'State2',
 'State3',
 'State4',
 'State5',
 'State6',
 'State7',
 'State8',
 'State9',
 'State10',
 'State11',
 'State12',
 'State13',
 'State14',
 'State15']

In [50]:
from datetime import datetime, timedelta

In [52]:
def calculate_cagr(start_value, end_value, period_years):
    if start_value == 0 or period_years == 0:
        return np.nan
    return (end_value / start_value) ** (1 / period_years) - 1

In [70]:
def calculate_rolling_cagr(df, return_period_years, window_size_days, start_from_years_ago = None):
    df["nav"] = df["Close"]
    df["date"] = pd.to_datetime(df.index)
    df = df.sort_values('date').reset_index(drop=True)

    if start_from_years_ago is not None:
      analysis_start_date = datetime.now() - timedelta(days=365 * start_from_years_ago)
      df = df[df['date'] >= analysis_start_date]
    
    end_dates = pd.date_range(start=df['date'].min() + timedelta(days=round(365*return_period_years)), 
                              end=df['date'].max(), freq=f'{window_size_days}D')
    
    cagr_values = []
    
    for end_date in end_dates:
        start_date = end_date - timedelta(days=round(365*return_period_years))
        
        nearest_start_idx = df['date'].searchsorted(start_date, side='left')
        nearest_end_idx = df['date'].searchsorted(end_date, side='right') - 1
        
        if nearest_start_idx < len(df) and nearest_end_idx < len(df):
            start_nav = df.iloc[nearest_start_idx]['nav']
            end_nav = df.iloc[nearest_end_idx]['nav']
            cagr = calculate_cagr(start_nav, end_nav, return_period_years)
            cagr_values.append(cagr)

    return np.nanmean(cagr_values)

### Algo

#### Strategy 1

    1. Using Price trend, MACD and EMA indicator

In [77]:
df2 = df.copy()

ema_entries = (df2.Close > df2.EMA20) & (df2.MACD > df2.MACD_SIGNAL) & (df2.MACD < 0) & (df2.MACD_SIGNAL < 0)
ema_exits = (df2.Close < df2.EMA20) & (df2.MACD < df2.MACD_SIGNAL) & (df2.MACD > 0) & (df2.MACD_SIGNAL > 0)

df2["TS_Entries"] = ema_entries
df2["TS_Exits"] = ema_exits
pf_tikr = vbt.Portfolio.from_signals(df2["Close"], entries=ema_entries, exits=ema_exits, freq="D", init_cash=100000, fees=0.0025, slippage=0.0025)
portfolio_return = pf_tikr.stats(settings=dict(required_return=0.1, risk_free=0.07))
portfolio_return = portfolio_return.to_frame().reset_index()
portfolio_return = portfolio_return.rename(columns= {0: 'VALUES'})
portfolio_return["COMPANY"]= '^NSEI'
portfolio_return.head(30)
pf_tikr.plot().show()

In [78]:
print(pf_tikr.returns_stats(settings=dict(required_return=0.1, risk_free=0.01)))

Start                                2013-01-22
End                                  2023-12-29
Period                       2686 days 00:00:00
Total Return [%]                     100.566328
Benchmark Return [%]                  259.28578
Annualized Return [%]                  9.919256
Annualized Volatility [%]              13.58076
Max Drawdown [%]                      20.315612
Max Drawdown Duration         686 days 00:00:00
Sharpe Ratio                         -26.111797
Calmar Ratio                           0.488258
Omega Ratio                            0.033287
Sortino Ratio                         -19.05663
Skew                                  -0.319356
Kurtosis                                5.31405
Tail Ratio                             1.045427
Common Sense Ratio                     1.149125
Value at Risk                         -0.011582
Alpha                                 -0.864343
Beta                                   0.449686
dtype: object


In [79]:
print(pf_tikr.stats(settings=dict(required_return=0.1, risk_free=0.07)))

Start                                 2013-01-22
End                                   2023-12-29
Period                        2686 days 00:00:00
Start Value                             100000.0
End Value                          200566.327787
Total Return [%]                      100.566328
Benchmark Return [%]                   259.28578
Max Gross Exposure [%]                     100.0
Total Fees Paid                      9941.598283
Max Drawdown [%]                       20.315612
Max Drawdown Duration          686 days 00:00:00
Total Trades                                  17
Total Closed Trades                           16
Total Open Trades                              1
Open Trade PnL                      31920.829105
Win Rate [%]                                50.0
Best Trade [%]                         46.227015
Worst Trade [%]                        -9.646337
Avg Winning Trade [%]                  13.709043
Avg Losing Trade [%]                   -5.433942
Avg Winning Trade Du

#### Strategy 2

    1.   Entry: (df2.MFI14 > 70) & ((df2.Close > df2.EMA100))
    2.   Exit: (df2.MFI14 < 30) & ((df2.Close < df2.EMA100))

In [72]:
df2 = df.copy()

ema_entries = (df2.MFI14 > 70) & ((df2.Close > df2.EMA100))
ema_exits = (df2.MFI14 < 30) & ((df2.Close < df2.EMA100))

df2["TS_Entries"] = ema_entries
df2["TS_Exits"] = ema_exits
pf_tikr = vbt.Portfolio.from_signals(df2.Close, entries=ema_entries, exits=ema_exits, freq="D", init_cash=100000, fees=0.0025, slippage=0.0025)
portfolio_return = pf_tikr.stats(settings=dict(required_return=0.1, risk_free=0.07))
portfolio_return = portfolio_return.to_frame().reset_index()
portfolio_return = portfolio_return.rename(columns= {0: 'VALUES'})
portfolio_return["COMPANY"]= '^NSEI'
portfolio_return.head(30)
pf_tikr.plot().show()

In [73]:
print(pf_tikr.returns_stats(settings=dict(required_return=0.1, risk_free=0.01)))

Start                                2013-01-22
End                                  2023-12-29
Period                       2686 days 00:00:00
Total Return [%]                     168.704841
Benchmark Return [%]                  259.28578
Annualized Return [%]                 14.375804
Annualized Volatility [%]             13.962927
Max Drawdown [%]                      18.420556
Max Drawdown Duration         542 days 00:00:00
Sharpe Ratio                         -25.108619
Calmar Ratio                           0.780422
Omega Ratio                            0.034754
Sortino Ratio                        -19.053769
Skew                                   -0.32054
Kurtosis                               4.785221
Tail Ratio                             1.044361
Common Sense Ratio                     1.194496
Value at Risk                         -0.011719
Alpha                                 -0.845622
Beta                                    0.47524
dtype: object


In [74]:
print(pf_tikr.stats(settings=dict(required_return=0.1, risk_free=0.07)))

Start                                          2013-01-22
End                                            2023-12-29
Period                                 2686 days 00:00:00
Start Value                                      100000.0
End Value                                   268704.840886
Total Return [%]                               168.704841
Benchmark Return [%]                            259.28578
Max Gross Exposure [%]                              100.0
Total Fees Paid                              10493.836081
Max Drawdown [%]                                18.420556
Max Drawdown Duration                   542 days 00:00:00
Total Trades                                           14
Total Closed Trades                                    13
Total Open Trades                                       1
Open Trade PnL                               49695.683072
Win Rate [%]                                    53.846154
Best Trade [%]                                  67.016638
Worst Trade [%

In [76]:
calculate_rolling_cagr(df2, 3, 14)

0.11966007520786663

#### Strategy 3



In [19]:
df2 = df.copy()

ema_entries = (df2.State1 > 0) & (df2.State7 > -0.3) & (df2.State12 > -0.1)
ema_exits = (df2.MFI14 < 30) & ((df2.Close < df2.EMA100)) & (df2.State11 < -0.1) & (df2.State7 < -0.3)

df2["TS_Entries"] = ema_entries
df2["TS_Exits"] = ema_exits
pf_tikr = vbt.Portfolio.from_signals(df2.Close, entries=ema_entries, exits=ema_exits, freq="D", init_cash=100000, fees=0.0025, slippage=0.0025)
portfolio_return = pf_tikr.stats(settings=dict(required_return=0.1, risk_free=0.07))
portfolio_return = portfolio_return.to_frame().reset_index()
portfolio_return = portfolio_return.rename(columns= {0: 'VALUES'})
portfolio_return["COMPANY"]= '^NSEI'
portfolio_return.head(30)
pf_tikr.plot().show()

In [20]:
print(pf_tikr.returns_stats(settings=dict(required_return=0.1, risk_free=0.01)))

Start                                2013-01-22
End                                  2023-12-29
Period                       2686 days 00:00:00
Total Return [%]                     315.650887
Benchmark Return [%]                  259.28578
Annualized Return [%]                 21.360937
Annualized Volatility [%]             16.584913
Max Drawdown [%]                      20.617545
Max Drawdown Duration         432 days 00:00:00
Sharpe Ratio                         -20.757394
Calmar Ratio                           1.036056
Omega Ratio                            0.055574
Sortino Ratio                        -19.032602
Skew                                  -0.138476
Kurtosis                               3.113567
Tail Ratio                              1.06307
Common Sense Ratio                     1.290152
Value at Risk                         -0.013543
Alpha                                 -0.671464
Beta                                   0.674576
dtype: object


In [21]:
print(pf_tikr.stats(settings=dict(required_return=0.1, risk_free=0.07)))

Start                                 2013-01-22
End                                   2023-12-29
Period                        2686 days 00:00:00
Start Value                             100000.0
End Value                          415650.886532
Total Return [%]                      315.650887
Benchmark Return [%]                   259.28578
Max Gross Exposure [%]                     100.0
Total Fees Paid                      6788.573387
Max Drawdown [%]                       20.617545
Max Drawdown Duration          432 days 00:00:00
Total Trades                                   8
Total Closed Trades                            7
Total Open Trades                              1
Open Trade PnL                      75192.639686
Win Rate [%]                           57.142857
Best Trade [%]                         75.524407
Worst Trade [%]                        -6.093327
Avg Winning Trade [%]                  42.760477
Avg Losing Trade [%]                    -4.04329
Avg Winning Trade Du

### AI

In [24]:
# Environment
class TradingEnvironment:
    def __init__(self, data, states=4):
        self.data = data
        self.n = len(self.data)
        self.index = 0
        self.invested = False
        self.last = 0
        self.states = states

    def reset(self):
        self.index = 0
        self.invested = False
        return self.get_state()

    def get_state(self):
        # Append the invested state as a float (0.0 for not invested, 1.0 for invested)
        current_state = self.data.iloc[self.index][[f"State{i}" for i in range(1, self.states)]].tolist()
        current_state.append(int(self.invested))  # Convert boolean to float and add to state
        return current_state

    def step(self, action):

        reward = 0

        benchmark_returns = self.data.iloc[self.index+1]['Close'] / self.data.iloc[self.index]['Close'] - 1

        if(action[0]):
            reward = (-1*benchmark_returns - 0.0025) * 1000
            self.last = self.index
            self.invested = False

        if(action[1]):
            reward = (benchmark_returns - 0.0025) * 1000
            self.last = self.index
            self.invested = True

        if(action[2]):
            if(self.invested):
                reward = (benchmark_returns) * 100
            if(not self.invested):
                reward = (-1*benchmark_returns) * 100
                if(self.index-self.last>1000): reward -= (self.index-self.last-1000)/100

        self.index += 1
        if self.index >= self.n - 1:
            done = True
        else:
            done = False

        next_state = self.get_state()
        return next_state, reward, done

    def calculate_cagr(self, ret, days=1):
        if(days==0): return 0
        years = days / 252
        return ((ret ** (1 / years)) - 1)

In [25]:
# AI Brain

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

class Linear_QNet(nn.Module):

    def __init__(self, input_size, hidden_size, output_size):
        super().__init__()
        self.linear1 = nn.Linear(input_size, hidden_size)
        self.linear2 = nn.Linear(hidden_size, output_size).to(device)

    def forward(self, x):
        x = F.relu(self.linear1(x))
        x = self.linear2(x)
        return x

    def save(self,filename='model.pth') :
        model_folder_path = "./model"
        if not os.path.exists(model_folder_path) :
            os.makedirs(model_folder_path)
        filename = os.path.join(model_folder_path,filename)
        torch.save(self.state_dict(),filename)

def load_model(input_size, hidden_size, output_size):
    model = Linear_QNet(input_size, hidden_size, output_size)
    model.load_state_dict(torch.load("model.pth"))
    return model.to(device)

class QTrainer:

    def __init__(self, model, lr, gamma):
        self.model = model.to(device)
        self.lr = lr
        self.gamma = gamma
        self.optimizer = optim.Adam(model.parameters(), lr=self.lr)
        self.criterion = nn.MSELoss()

    def train_step(self, state, action, reward, next_state, done):
        state = torch.tensor(state, dtype=torch.float)
        next_state = torch.tensor(next_state, dtype=torch.float)
        action = torch.tensor(action, dtype=torch.long)
        reward = torch.tensor(reward, dtype=torch.float)

        if(len(state.shape)==1) :
            state = torch.unsqueeze(state,0)
            next_state = torch.unsqueeze(next_state,0)
            action = torch.unsqueeze(action,0)
            reward = torch.unsqueeze(reward,0)
            done = (done, )

        state = state.to(device)
        next_state = next_state.to(device)
        action = action.to(device)
        reward = reward.to(device)

        pred = self.model(state)

        target = pred.clone()

        for idx in range(len(done)) :
            Q_new = reward[idx]
            if not done[idx] :
                Q_new = reward[idx] + self.gamma*torch.max(self.model(next_state[idx]))

            target[idx][torch.argmax(action).item()] = Q_new

        self.optimizer.zero_grad()
        loss = self.criterion(pred, target)
        loss.backward()

        self.optimizer.step()

In [31]:
# AI Agent and Learning

MAX_MEMORY = 25000
BATCH_SIZE = 2000
LR = 0.01
GAMMA = 0.9
EPOCHS = 1000

# Agent class
class Agent:
    def __init__(self, input_size, hidden_size, output_size, lr, gamma):
        self.output_size = output_size
        self.model = Linear_QNet(input_size, hidden_size, output_size).to(device)
        self.trainer = QTrainer(self.model, lr, gamma)
        self.df = getData()
        self.env = TradingEnvironment(self.df,input_size)
        self.state = self.env.reset()
        self.epsilon = 0
        self.n = 0
        self.memory = deque(maxlen=MAX_MEMORY) # popleft()
        self.bestReturn = 0
        self.stats = []

    def get_state(self):
        return self.env.get_state()


    def train(self, episodes):
        # self.epochResult(0)

        for e in range(episodes):
            self.env.reset()
            done = False
            while not done:

                state_old = self.get_state()
                final_move = self.get_action(state_old,True)

                state_new, reward, done = self.env.step(final_move)

                self.train_short_memory(state_old,final_move,reward,state_new,done)

                self.remember(state_old,final_move,reward,state_new,done)

                self.n += 1

            self.train_long_memory()
            self.epochResult(e+1)


    def remember(self,state,action,reward,next_state,done) :
        self.memory.append((state,action,reward,next_state,done))


    def train_long_memory(self) :
        if(len(self.memory)>BATCH_SIZE) :
            mini_sample = random.sample(self.memory,BATCH_SIZE)
        else :
            mini_sample = self.memory

        states,actions,rewards,next_states,dones = zip(*mini_sample)
        self.trainer.train_step(states,actions,rewards,next_states,dones)

    def train_short_memory(self,state,action,reward,next_state,done) :
        self.trainer.train_step(state,action,reward,next_state,done)

    def epochResult(self, e):
        state = self.env.reset()
        done = False
        trades = []
        invested = False

        while not done:
            action = self.get_action(state)
            next_state, _, done = self.env.step(action)
            if action[1]:
                invested = True
            elif action[0]:
                invested = False
            trades.append(invested)
            state = next_state

        trades = trades + [trades[-1]]
        trades[0] = False
        mn =  sum(trades)/len(trades)
        df2 = self.df.copy()
        df2['GC'] = trades
        golden = df2.ta.tsignals(df2.GC, asbool=True, append=True)

        pf_tikr = vbt.Portfolio.from_signals(df2['Close'], entries=df2['TS_Entries'], exits=df2['TS_Exits'], freq="D", init_cash=100, fees=0.0025, slippage=0.0025)
        portfolio_return = pf_tikr.stats(settings=dict(required_return=0.1, risk_free=0.07))
        portfolio_return = portfolio_return.to_frame().reset_index()
        portfolio_return = portfolio_return.rename(columns= {0: 'VALUES'})
        portfolio_return["COMPANY"]= '^NSEI'
        ret = pf_tikr.returns_stats(settings=dict(required_return=0.1, risk_free=0.01))['Annualized Return [%]']

        if(ret > self.bestReturn):
            self.bestReturn = ret
            self.model.save()

        self.stats.append({'Epoch':e, 'Invested':round(mn,2), 'CAGR': round(ret,1), 'Best': round(self.bestReturn,1)})

        with open('stats.json', 'w') as f:
            json.dump(self.stats, f)

        print("Epoch {:.0f} | Invested: {:.2f} | Annualized Return: {:.1f} | Best Return: {:.1f}".format(e,mn,ret,self.bestReturn))


    def get_action(self, state, isTrain=False):
        final_move = [0,0,0]
        # if(isTrain):
        self.epsilon = max(0,3)
        if random.randint(0,200) < self.epsilon :
          move =  random.randint(0,1)
          final_move[move] = 1
          return final_move
        state_tensor = torch.tensor(state, dtype=torch.float).unsqueeze(0).to(device)
        output = self.model(state_tensor)
        move = torch.argmax(output).item()
        final_move[move] = 1
        return final_move

def train() :
    agent = Agent(input_size=16, hidden_size=128, output_size=3, lr=LR, gamma=GAMMA)
    agent.train(episodes=EPOCHS)

In [21]:
AI_Trader = Agent(input_size=16, hidden_size=128, output_size=3, lr=LR, gamma=GAMMA)
AI_Trader.model = load_model(input_size=16, hidden_size=128, output_size=3)

state = AI_Trader.env.reset()
done = False
trades = []
invested = False

while not done:
    action = AI_Trader.get_action(state)
    next_state, _, done = AI_Trader.env.step(action)
    if action[1]:
        invested = True
    elif action[0]:
        invested = False
    trades.append(invested)
    state = next_state

trades = trades + [trades[-1]]
trades[0] = False
mn =  sum(trades)/len(trades)
df2 = AI_Trader.df.copy()
df2['GC'] = trades
golden = df2.ta.tsignals(df2.GC, asbool=True, append=True)

pf_tikr = vbt.Portfolio.from_signals(df2['Close'], entries=df2['TS_Entries'], exits=df2['TS_Exits'], freq="D", init_cash=100000, fees=0.0025, slippage=0.0025)
portfolio_return = pf_tikr.stats(settings=dict(required_return=0.1, risk_free=0.07))
portfolio_return = portfolio_return.to_frame().reset_index()
portfolio_return = portfolio_return.rename(columns= {0: 'VALUES'})
portfolio_return["COMPANY"]= '^NSEI'

In [22]:
pf_tikr.plot().show()

In [23]:
print(pf_tikr.returns_stats(settings=dict(required_return=0.1, risk_free=0.01)))

Start                                2013-01-22
End                                  2023-12-29
Period                       2686 days 00:00:00
Total Return [%]                     291.525185
Benchmark Return [%]                  259.28578
Annualized Return [%]                 20.378796
Annualized Volatility [%]             17.906096
Max Drawdown [%]                      38.439852
Max Drawdown Duration         545 days 00:00:00
Sharpe Ratio                         -19.257839
Calmar Ratio                           0.530148
Omega Ratio                            0.063482
Sortino Ratio                        -19.020718
Skew                                   -1.15344
Kurtosis                              25.296127
Tail Ratio                             1.131742
Common Sense Ratio                     1.362378
Value at Risk                         -0.012752
Alpha                                 -0.509559
Beta                                   0.791884
dtype: object


In [24]:
print(pf_tikr.stats(settings=dict(required_return=0.1, risk_free=0.07)))

Start                                 2013-01-22
End                                   2023-12-29
Period                        2686 days 00:00:00
Start Value                             100000.0
End Value                          391525.185477
Total Return [%]                      291.525185
Benchmark Return [%]                   259.28578
Max Gross Exposure [%]                     100.0
Total Fees Paid                      8968.245943
Max Drawdown [%]                       38.439852
Max Drawdown Duration          545 days 00:00:00
Total Trades                                   8
Total Closed Trades                            7
Total Open Trades                              1
Open Trade PnL                      25907.150667
Win Rate [%]                           71.428571
Best Trade [%]                         62.814563
Worst Trade [%]                        -3.435981
Avg Winning Trade [%]                  33.670531
Avg Losing Trade [%]                   -3.297805
Avg Winning Trade Du

In [258]:
calculate_CAGR(100000, 391525, 12)

12.046069105251767

### AI + Algo

In [41]:
df2 = df.copy()

ema_entries = (df2.MFI14 > 50) 
ema_exits = (df2.MFI14 < 50) 

In [42]:
AI_Trader = Agent(input_size=16, hidden_size=128, output_size=3, lr=LR, gamma=GAMMA)
AI_Trader.model = load_model(input_size=16, hidden_size=128, output_size=3)

state = AI_Trader.env.reset()
done = False
trades = []
invested = False
idx = 0

while not done:
    action = AI_Trader.get_action(state)
    next_state, _, done = AI_Trader.env.step(action)
    if action[1] or ema_entries[idx]:
        invested = True
    elif action[0] and ema_exits[idx]:
        invested = False
    trades.append(invested)
    state = next_state
    idx += 1

trades = trades + [trades[-1]]
trades[0] = False
mn =  sum(trades)/len(trades)
df2 = AI_Trader.df.copy()
df2['GC'] = trades
golden = df2.ta.tsignals(df2.GC, asbool=True, append=True)

pf_tikr = vbt.Portfolio.from_signals(df2['Close'], entries=df2['TS_Entries'], exits=df2['TS_Exits'], freq="D", init_cash=100000, fees=0.0025, slippage=0.0025)
portfolio_return = pf_tikr.stats(settings=dict(required_return=0.1, risk_free=0.07))
portfolio_return = portfolio_return.to_frame().reset_index()
portfolio_return = portfolio_return.rename(columns= {0: 'VALUES'})
portfolio_return["COMPANY"]= '^NSEI'

In [43]:
pf_tikr.plot().show()

In [44]:
print(pf_tikr.returns_stats(settings=dict(required_return=0.1, risk_free=0.01)))

Start                                2013-01-22
End                                  2023-12-29
Period                       2686 days 00:00:00
Total Return [%]                     223.837193
Benchmark Return [%]                  259.28578
Annualized Return [%]                 17.313555
Annualized Volatility [%]              20.01616
Max Drawdown [%]                      38.439852
Max Drawdown Duration         575 days 00:00:00
Sharpe Ratio                         -17.336566
Calmar Ratio                           0.450406
Omega Ratio                            0.072817
Sortino Ratio                        -18.999989
Skew                                  -0.957666
Kurtosis                               16.03168
Tail Ratio                             1.010726
Common Sense Ratio                     1.185719
Value at Risk                         -0.015314
Alpha                                   -0.0553
Beta                                    0.98769
dtype: object


In [45]:
print(pf_tikr.stats(settings=dict(required_return=0.1, risk_free=0.07)))

Start                                 2013-01-22
End                                   2023-12-29
Period                        2686 days 00:00:00
Start Value                             100000.0
End Value                          323837.192634
Total Return [%]                      223.837193
Benchmark Return [%]                   259.28578
Max Gross Exposure [%]                     100.0
Total Fees Paid                      4227.602756
Max Drawdown [%]                       38.439852
Max Drawdown Duration          575 days 00:00:00
Total Trades                                   7
Total Closed Trades                            6
Total Open Trades                              1
Open Trade PnL                     168391.778028
Win Rate [%]                           83.333333
Best Trade [%]                         29.688694
Worst Trade [%]                        -0.661435
Avg Winning Trade [%]                   9.841235
Avg Losing Trade [%]                   -0.661435
Avg Winning Trade Du

**END OF PROJECT**